In [1]:
import numpy as np

In [2]:
from pathlib import Path
import pickle

num_datapoints_per_file = 500

# Loading the files back in
observations = []
binding_affinities = []

NPYS_FOLDER = Path('/usr/project/dlab/Users/jaden/gbr-tnet/persistence/persistence_images')

for file_index in range(len(list(NPYS_FOLDER.glob('binding_affinities_*.npy')))):
    with open(NPYS_FOLDER / f'observations_{file_index}.npy', 'rb') as f:
        observations.append(np.load(f))

    with open(NPYS_FOLDER / f'binding_affinities_{file_index}.npy', 'rb') as f:
        binding_affinities.append(np.load(f))


In [3]:
observations = np.concatenate(observations)
binding_affinities = np.concatenate(binding_affinities)

print(observations.shape)
print(binding_affinities.shape)


(5190, 40, 3, 10000)
(5190,)


In [4]:
observations = observations.reshape(observations.shape[0], -1)
observation_indices = np.arange(observations.shape[1])

In [40]:
print(observations.shape)
print(binding_affinities.shape)

(5190, 1200000)
(5190,)


In [5]:
highly_selected_observations_indices = [16829, 16930, 17031, 17818, 17819, 17917, 17918, 17919, 17920, 18019, 18020, 18021, 18115, 18116, 18117, 18120, 18121, 18214, 18215, 18216, 18217, 18218, 18313, 18314, 18315, 18316, 18317, 18318, 18413, 18415, 18416, 18417, 18418, 18514, 18516, 18517, 18610, 18615, 18710, 18711, 18811, 18812, 18908, 18912, 18913, 19110, 287524, 287620, 287719, 287720, 287721, 287818, 287821, 287822, 287919, 287921, 287922, 287923, 288020, 288022, 288121, 288219, 288314, 288415, 288516, 31500, 31700, 31701, 31702, 61301, 91000, 91001, 91002, 91802, 92100, 92101, 92102]

highly_selected_observations = observations[:, highly_selected_observations_indices]
highly_selected_observations_indices = observation_indices[highly_selected_observations_indices]

In [6]:
print(highly_selected_observations.shape, highly_selected_observations_indices.shape, sep='\n')

(5190, 77)
(77,)


In [7]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingRegressor
import plotly.express as px
from sklearn.metrics import r2_score

In [8]:
stats = []

from tqdm import tqdm
from multiprocessing import Pool, cpu_count

Path('additional_results').mkdir(exist_ok=True)

def trial(i):
    X_train, X_test, y_train, y_test = train_test_split(highly_selected_observations, binding_affinities, test_size=0.1, random_state=i)
    regr = GradientBoostingRegressor(random_state=2*i)
    regr.fit(X_train, y_train)

    y_hat = regr.predict(X_test)

    r2 = r2_score(y_test, y_hat)
    rmse = np.sqrt(np.mean((y_test - y_hat)**2))
    pearson = np.corrcoef(y_test, y_hat)[0, 1]

    fig = px.scatter(x=y_test, y=y_hat, labels={'x': 'True binding affinity', 'y': 'Predicted binding affinity'}, title=f'True vs Predicted binding affinity\nR^2 = {r2_score(y_test, y_hat):.2f}, n = {len(y_test)}, RMSE: {np.sqrt(np.mean((y_test - y_hat)**2)):.2f}, Pearson: {np.corrcoef(y_test, y_hat)[0, 1]:.2f}')
    fig.write_html(f'additional_results/GBR_strong_ablated_results_{i}.html')

    return {'r2': r2, 'rmse': rmse, 'pearson': pearson}


with Pool(cpu_count()- 4) as p:
    stats = p.map(trial, range(100))

rmses = [s['rmse'] for s in stats]
r2s = [s['r2'] for s in stats]
pearsons = [s['pearson'] for s in stats]

print(f'RMSE: {np.mean(rmses):.4f} +/- {np.std(rmses):.4f}')
print(f'R2: {np.mean(r2s):.4f} +/- {np.std(r2s):.4f}')
print(f'Pearson: {np.mean(pearsons):.4f} +/- {np.std(pearsons):.4f}')

RMSE: 1.4419 +/- 0.0429
R2: 0.4499 +/- 0.0321
Pearson: 0.6723 +/- 0.0243


### Start from 77-dimensional vector

At each iteration, ablate the least helpful element while keeping track of which index was thrown away

In [9]:
from tqdm import tqdm

def train_and_test(observations, binding_affinities, num_runs=10):
    stats = []

    for i in range(num_runs):
        X_train, X_test, y_train, y_test = train_test_split(observations, binding_affinities, test_size=0.1, random_state=i)
        regr = GradientBoostingRegressor(random_state=2*i)
        regr.fit(X_train, y_train)

        y_hat = regr.predict(X_test)

        r2 = r2_score(y_test, y_hat)
        rmse = np.sqrt(np.mean((y_test - y_hat)**2))
        pearson = np.corrcoef(y_test, y_hat)[0, 1]

        stats.append({'r2': r2, 'rmse': rmse, 'pearson': pearson})

    rmses = [s['rmse'] for s in stats]
    r2s = [s['r2'] for s in stats]
    pearsons = [s['pearson'] for s in stats]

    results = {
        'rmse': {
            'mean': np.mean(rmses),
            'std': np.std(rmses)
        },
        'r2': {
            'mean': np.mean(r2s),
            'std': np.std(r2s)
        },
        'pearson': {
            'mean': np.mean(pearsons),
            'std': np.std(pearsons)
        }
    }

    return results

In [10]:
from multiprocessing import Pool, cpu_count

# # This takes a while, but I save the results into a pickle file to load later

# print(f'Using {cpu_count() - 4} cores')

# # starting with highly_selected_observations
# # 10 runs for each ablated element

# assert highly_selected_observations.shape[1] == len(highly_selected_observations_indices)

# ablation_iter_results = []  # Keeps track of results for each iteration of ablation

# # ablate one element at a time
# for iter in range(highly_selected_observations.shape[1] - 1):
#     print(f'Starting iteration {iter}')

#     def ablate_run(index):
#         ablated_observations = np.delete(highly_selected_observations, index, axis=1)
#         ablation_result = train_and_test(ablated_observations, binding_affinities, num_runs=10)
#         return ablation_result

#     with Pool(cpu_count() - 4) as p:
#         ablation_results = p.map(ablate_run, range(highly_selected_observations.shape[1]))

#     with open(f'additional_results/ablation_results_{iter}.pkl', 'wb') as f:
#         pickle.dump(ablation_results, f)

#     # Find index with lowest RMSE (and thus the least important feature)
#     min_rmse_index = np.argmin([r['rmse']['mean'] for r in ablation_results])
#     min_rmse = ablation_results[min_rmse_index]['rmse']['mean']
#     min_rmse_std = ablation_results[min_rmse_index]['rmse']['std']

#     print(f'Finished iteration {iter}, deleted index {min_rmse_index} (original index {highly_selected_observations_indices[min_rmse_index]}), new RMSE: {min_rmse:.4f} +/- {min_rmse_std:.4f}')

#     # Delete that index
#     highly_selected_observations = np.delete(highly_selected_observations, min_rmse_index, axis=1)
#     highly_selected_observations_indices = np.delete(highly_selected_observations_indices, min_rmse_index)

#     ablation_iter_results.append({
#         'min_rmse_index': min_rmse_index,
#         'iteration_results': ablation_results[min_rmse_index],
#         'remaining_indices': highly_selected_observations_indices
#     })

#     with open(f'ablation_iter_results.pkl', 'wb') as f:
#         pickle.dump(ablation_iter_results, f)


with open(f'ablation_iter_results.pkl', 'rb') as f:
    ablation_iter_results = pickle.load(f)

In [15]:
# Plot rmse vs number of remaining features

import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Scatter(x=77 - np.arange(len(ablation_iter_results)), y=[r['iteration_results']['rmse']['mean'] for r in ablation_iter_results], error_y=dict(type='data', array=[r['iteration_results']['rmse']['std'] for r in ablation_iter_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of remaining features<br>Error bars are standard deviation of RMSE over 50 runs.',
    xaxis_title='Number of features in vector',
    yaxis_title='RMSE'
)

fig.show()

In [16]:
list(filter(lambda x: len(x['remaining_indices']) == 10, ablation_iter_results))[0]

{'min_rmse_index': 4,
 'iteration_results': {'rmse': {'mean': 1.437934215527271,
   'std': 0.035322301749220485},
  'r2': {'mean': 0.44710696440878805, 'std': 0.0322590753870504},
  'pearson': {'mean': 0.6701473245326413, 'std': 0.02445064877016254}},
 'remaining_indices': array([ 17819,  18318,  18514,  18908, 288020, 288516,  31500,  31702,
         61301,  91001])}

### Exploration with the tiny subset of features

In [17]:
tiny_feature_subset_indices = [ 17819,  18318,  18514,  18908, 288020, 288516,  31500,  31702, 61301,  91001]

tiny_feature_subset = observations[:, tiny_feature_subset_indices]

In [18]:
from tqdm import tqdm
from multiprocessing import Pool, cpu_count


def trial(i):
    X_train, X_test, y_train, y_test = train_test_split(tiny_feature_subset, binding_affinities, test_size=0.1)
    regr = GradientBoostingRegressor()
    regr.fit(X_train, y_train)

    y_hat = regr.predict(X_test)

    r2 = r2_score(y_test, y_hat)
    rmse = np.sqrt(np.mean((y_test - y_hat)**2))
    pearson = np.corrcoef(y_test, y_hat)[0, 1]

    return {'r2': r2, 'rmse': rmse, 'pearson': pearson}

with Pool(cpu_count() - 4) as p:
    stats = p.map(trial, range(400))

rmses = [s['rmse'] for s in stats]
r2s = [s['r2'] for s in stats]
pearsons = [s['pearson'] for s in stats]

results = {
    'rmse': {
        'mean': np.mean(rmses),
        'std': np.std(rmses)
    },
    'r2': {
        'mean': np.mean(r2s),
        'std': np.std(r2s)
    },
    'pearson': {
        'mean': np.mean(pearsons),
        'std': np.std(pearsons)
    }
}


In [19]:
print(f'Results after 400 runs: ')

results

Results after 400 runs: 


{'rmse': {'mean': 1.476146838831787, 'std': 0.02056301066694162},
 'r2': {'mean': 0.454480435147095, 'std': 0.023721033853316125},
 'pearson': {'mean': 0.6758825143665094, 'std': 0.01889011870220535}}

### Hyperparameter search

First try: Reducing the number of estimators

In [20]:
def train_and_test_reduce_estimators(n_estimators, gbr_kwargs={}, n_trials=10):
    stats = []

    for i in range(n_trials):
        X_train, X_test, y_train, y_test = train_test_split(tiny_feature_subset, binding_affinities, test_size=0.1, random_state=i)
        regr = GradientBoostingRegressor(n_estimators=n_estimators, random_state=2*i, **gbr_kwargs)
        regr.fit(X_train, y_train)

        y_hat = regr.predict(X_test)

        r2 = r2_score(y_test, y_hat)
        rmse = np.sqrt(np.mean((y_test - y_hat)**2))
        pearson = np.corrcoef(y_test, y_hat)[0, 1]

        stats.append({'r2': r2, 'rmse': rmse, 'pearson': pearson})

    rmses = [s['rmse'] for s in stats]
    r2s = [s['r2'] for s in stats]
    pearsons = [s['pearson'] for s in stats]

    results = {
        'n_estimators': n_estimators,
        'rmse': {
            'mean': np.mean(rmses),
            'std': np.std(rmses)
        },
        'r2': {
            'mean': np.mean(r2s),
            'std': np.std(r2s)
        },
        'pearson': {
            'mean': np.mean(pearsons),
            'std': np.std(pearsons)
        }
    }

    return results


In [21]:
# Plot RMSE and stdev vs number of estimators
with Pool(cpu_count()) as p:
    reduce_estimator_results = p.map(train_and_test_reduce_estimators, range(1, 100))

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>3</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()


In [22]:
# Setting tree depth to 6

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 6}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>6</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [23]:
# Setting tree depth to 9

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 9}) for i in range(1, 100)])

In [24]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>9</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()


<!-- It seems that with **10** features, we can get an RMSE of 1.50 using
- A tree depth of **6** with **22** estimators, or
- A tree depth of **9** with **17** estimators -->

Let's increase the learning rate (default is 0.1)

In [25]:
# tree depth = 3, lr = 0.2

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 3, 'learning_rate': 0.2}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>3</b>. Learning Rate: <b>0.2</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [26]:
# tree depth = 3, lr = 0.3

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 3, 'learning_rate': 0.3}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>3</b>. Learning Rate: <b>0.3</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [27]:
# tree depth = 3, lr = 0.4

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 3, 'learning_rate': 0.4}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>3</b>. Learning Rate: <b>0.4</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [28]:
# tree depth = 3, lr = 0.5

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 3, 'learning_rate': 0.5}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>3</b>. Learning Rate: <b>0.5</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [29]:
# tree depth = 6, lr = 0.2

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 6, 'learning_rate': 0.2}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>6</b>. Learning Rate: <b>0.2</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [30]:
# tree depth = 9, lr = 0.2

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 9, 'learning_rate': 0.2}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>9</b>. Learning Rate: <b>0.2</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [31]:
# tree depth = 6, lr = 0.3

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 6, 'learning_rate': 0.3}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>6</b>. Learning Rate: <b>0.3</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [32]:
# tree depth = 9, lr = 0.3

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 9, 'learning_rate': 0.3}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>9</b>. Learning Rate: <b>0.3</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [33]:
# tree depth = 6, lr = 0.6

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 6, 'learning_rate': 0.6}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>6</b>. Learning Rate: <b>0.6</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [34]:
# tree depth = 9, lr = 0.6

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 9, 'learning_rate': 0.6}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>9</b>. Learning Rate: <b>0.6</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [35]:
# tree depth = 6, lr = 0.9

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 6, 'learning_rate': 0.9}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>6</b>. Learning Rate: <b>0.9</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

In [36]:
# tree depth = 9, lr = 0.9

with Pool(cpu_count()) as p:
    reduce_estimator_results = p.starmap(train_and_test_reduce_estimators, [(i, {'max_depth': 9, 'learning_rate': 0.9}) for i in range(1, 100)])

fig = go.Figure()

fig.add_trace(go.Scatter(x=[r['n_estimators'] for r in reduce_estimator_results], y=[r['rmse']['mean'] for r in reduce_estimator_results], error_y=dict(type='data', array=[r['rmse']['std'] for r in reduce_estimator_results]), mode='markers+lines'))

fig.update_layout(
    title='RMSE vs number of estimators. Tree depth: <b>9</b>. Learning Rate: <b>0.9</b><br>Error bars are standard deviation of RMSE over 10 runs.',
    xaxis_title='Number of estimators',
    yaxis_title='RMSE'
)

fig.show()

<!-- In the end, the best performing estimator at RMSE of 1.5 seems to have the hyperparameters:
- Max depth: **6**
- Number of estimators: **11**
- Learning rate: **0.2**

Let's train that model again -->

In [37]:
hyperparams_dict_to_string = lambda d: '__'.join([f'{k}_{v}' for k, v in d.items()])

In [38]:
gbr_kwargs = {'max_depth': 3, 'learning_rate': 0.4, 'n_estimators': 13}

X_train, X_test, y_train, y_test = train_test_split(tiny_feature_subset, binding_affinities, test_size=0.1, random_state=4)  # It seems that the RMSE strongly depends on the random state of the train-test split
regr = GradientBoostingRegressor(random_state=5, **gbr_kwargs)
regr.fit(X_train, y_train)

y_hat = regr.predict(X_test)

r2 = r2_score(y_test, y_hat)
rmse = np.sqrt(np.mean((y_test - y_hat)**2))
pearson = np.corrcoef(y_test, y_hat)[0, 1]

print(f'R2: {r2:.4f}, RMSE: {rmse:.4f}, Pearson: {pearson:.4f}')

from sklearn.tree import export_graphviz
from pathlib import Path

trees_save_folder = f'trees/tree_{hyperparams_dict_to_string(gbr_kwargs)}'
print(f'Saving to {trees_save_folder}')

Path(trees_save_folder).mkdir(parents=True, exist_ok=True)
for i in range(len(regr.estimators_)):
    export_graphviz(regr.estimators_[i, 0], out_file=f'{trees_save_folder}/{i}.dot')

R2: 0.4577, RMSE: 1.4287, Pearson: 0.6787
Saving to trees/tree_max_depth_3__learning_rate_0.4__n_estimators_13


In [39]:
# Do KNN

from sklearn.neighbors import KNeighborsRegressor

stats = []

for i in tqdm(range(100)):
    X_train, X_test, y_train, y_test = train_test_split(tiny_feature_subset, binding_affinities, test_size=0.1, random_state=i)
    regr = KNeighborsRegressor(30)
    regr.fit(X_train, y_train)

    y_hat = regr.predict(X_test)

    r2 = r2_score(y_test, y_hat)
    rmse = np.sqrt(np.mean((y_test - y_hat)**2))
    pearson = np.corrcoef(y_test, y_hat)[0, 1]

    stats.append({'r2': r2, 'rmse': rmse, 'pearson': pearson})

rmses = [s['rmse'] for s in stats]
r2s = [s['r2'] for s in stats]
pearsons = [s['pearson'] for s in stats]

results = {
    'rmse': {
        'mean': np.mean(rmses),
        'std': np.std(rmses)
    },
    'r2': {
        'mean': np.mean(r2s),
        'std': np.std(r2s)
    },
    'pearson': {
        'mean': np.mean(pearsons),
        'std': np.std(pearsons)
    }
}

print(results)

# KNN with 10 nearest neighbors seems to also be decent in terms of RMSE

  0%|          | 0/100 [00:00<?, ?it/s]

100%|██████████| 100/100 [00:01<00:00, 67.51it/s]

{'rmse': {'mean': 1.5727537554585838, 'std': 0.04002329390596312}, 'r2': {'mean': 0.3456769760006543, 'std': 0.03386378360400608}, 'pearson': {'mean': 0.5906848993806898, 'std': 0.026942848879839675}}


In [55]:
reference_arr = np.array([[f'({i}, {j})' for i in range(100)] for j in range(100)])
reference_arr = reference_arr.flatten()

get_coordinates = lambda index: reference_arr[index]


protein_heavy_elements = ['C', 'N', 'O', 'S']
ligand_heavy_elements = ['C', 'N', 'O', 'S', 'F', 'P', 'Cl', 'Br', 'I']

diagrams = []

for pe in protein_heavy_elements:
    for le in ligand_heavy_elements:
        diagrams.append([pe, le])

def find_diagram_type(diagram_index):
    diagram_num = int(diagram_index / 3)
    if diagram_num < 36:
        return f'Opposition homology with element types: {diagrams[diagram_num]}. Dimension: {diagram_index % 3}'
    else:
        return f'2345 homology with type: {diagram_num - 36 + 2} (check GWW 2017 for 2345 homology meaning). Dimension: {diagram_index % 3}'

for i, index in enumerate(tiny_feature_subset_indices):
    diagram_index = int(index / 10000)
    print(f'Index in vec: {i}. Index: {index}. Diagram index: {diagram_index}. Diagram type: {find_diagram_type(diagram_index)}. Coordinates within diagram: {get_coordinates(index % 10000)}')


Index in vec: 0. Index: 17819. Diagram index: 1. Diagram type: Opposition homology with element types: ['C', 'C']. Dimension: 1. Coordinates within diagram: (19, 78)
Index in vec: 1. Index: 18318. Diagram index: 1. Diagram type: Opposition homology with element types: ['C', 'C']. Dimension: 1. Coordinates within diagram: (18, 83)
Index in vec: 2. Index: 18514. Diagram index: 1. Diagram type: Opposition homology with element types: ['C', 'C']. Dimension: 1. Coordinates within diagram: (14, 85)
Index in vec: 3. Index: 18908. Diagram index: 1. Diagram type: Opposition homology with element types: ['C', 'C']. Dimension: 1. Coordinates within diagram: (8, 89)
Index in vec: 4. Index: 288020. Diagram index: 28. Diagram type: Opposition homology with element types: ['N', 'C']. Dimension: 1. Coordinates within diagram: (20, 80)
Index in vec: 5. Index: 288516. Diagram index: 28. Diagram type: Opposition homology with element types: ['N', 'C']. Dimension: 1. Coordinates within diagram: (16, 85)
I

In [58]:
import plotly.express as px

diagram_index = 28
# Plot the persistence image (2D vector), additionally label each pixel with their index in the flattened vector
# observations[0][1]

diagram_index_to_range = lambda x: np.arange(x*10000, (x+1)*10000)
px.imshow(observations[0][diagram_index_to_range(diagram_index)].reshape(100, 100))


In [49]:
# Just as a legend to show the indices

import plotly.express as px

px.imshow(np.arange(10000).reshape(100, 100))

In [ ]:
import sys

sys.path.append('../..')

import svm_ph

pdb_file = '/usr/project/dlab/Users/jaden/pdbbind/refined-set/1a4k/1a4k_protein.pdb'
mol2_file = '/usr/project/dlab/Users/jaden/pdbbind/refined-set/1a4k/1a4k_ligand.mol2'

diagrams = svm_ph.get_persistence_diagrams(pdb_file, mol2_file)

In [ ]:
betti_1_diagrams = list(filter(lambda x: x[2] == 1, diagrams[0][0]))
betti_1_diagrams

[array([111.55921936, 200.        ,   1.        ]),
 array([111.04740143, 200.        ,   1.        ]),
 array([110.81421661, 200.        ,   1.        ]),
 array([110.31800079, 200.        ,   1.        ]),
 array([109.98413849, 200.        ,   1.        ]),
 array([109.90579224, 200.        ,   1.        ]),
 array([109.88147736, 200.        ,   1.        ]),
 array([109.77754211, 200.        ,   1.        ]),
 array([109.76281738, 200.        ,   1.        ]),
 array([109.70331573, 200.        ,   1.        ]),
 array([109.57192993, 200.        ,   1.        ]),
 array([109.5473175, 200.       ,   1.       ]),
 array([109.36717987, 200.        ,   1.        ]),
 array([109.32941437, 200.        ,   1.        ]),
 array([109.24974823, 200.        ,   1.        ]),
 array([109.23052216, 200.        ,   1.        ]),
 array([109.20775604, 200.        ,   1.        ]),
 array([109.20235443, 200.        ,   1.        ]),
 array([109.16202545, 200.        ,   1.        ]),
 array([109.146

In [ ]:
import plotly.express as px

px.histogram(list(map(lambda x: x[0], betti_1_diagrams)))

In [ ]:
from gtda.diagrams import PersistenceImage

pim = PersistenceImage()

# Plot

xt = pim.fit_transform(diagrams[0])
pim.plot(xt, homology_dimension_idx=1)

In [ ]:
pim.plot(xt, homology_dimension_idx=0)

- C-C PWO Dim 1: x = 5 (idx = 605)
- C-C PWO Dim 1: x = 11 (idx = 1211)
- C-C PWO Dim 1: x = 35 (idx = 3635)
- C-C PWO Dim 0: x = TBD (idx = 1501)
- C-N PWO Dim 0: x = TBD (idx = 8800)
- N-C PWO Dim 1: x = 11 (idx = 1211)
- S-O PWO Dim 0: x = TBD (idx = 100)
- S-O PWO Dim 0: x = TBD (idx = 9902)
- 'Diagram index in final filter: 5. The 6001th element of 2345 homology with type: 3 (check GWW 2017 for 2345 homology meaning). Dimension: 1',
- 'Diagram index in final filter: 5. The 7201th element of 2345 homology with type: 3 (check GWW 2017 for 2345 homology meaning). Dimension: 1'